<center><b><font size=6>Lab-6 A classifier from scratch<b><center>

### Objective: Implement, use and evaluate a classifier (without using specific libraries such as sklearn)
1. **Logistic regression** is a binary classification method that maps a linear combination of parameters and variables into two possible classes. Here, you will implement the logistic regression from scratch to better understand how an ML algorithm works. Useful link: <a href="https://en.wikipedia.org/wiki/Logistic_regression">Wiki</a>.
2. **Performance evaluation metrics** are needed to evaluate the outcome of prediction with respect to true labels. Here, you will implement confusion matrix, accuracy, precision, recall and F-measure. Useful link: <a href="https://en.wikipedia.org/wiki/Confusion_matrix">Wiki</a>.

In [1]:
# import needed python libraries

%matplotlib inline

import pandas as pd
import seaborn as sns
import numpy as np
import matplotlib.pyplot as plt
import random

### 1. Dataset - TCP logs
The dataset contains traffic information generated by an open-source passive network monitoring tool, namely **tstat**. It automates the collection of packet statistics of traffic aggregates, using real-time monitoring features. Being a passive tool, the typical usage scenario is live monitoring of Internet links, in which all transmitted packets are observed. In case of TCP, Tstat identifies a new flow start when it observes a TCP three-way handshake. Similarly, it identifies a TCP flow end either when it sees the TCP connection teardown, or when it doesn’t observe packets for some time (idle time). A flow is defined by a unique link between the sender and receiver, e.g., a tuple of <em>(IP_Protocol_Type, IP_Source_Address, Source_Port, IP_Destination_Address, Destination_Port)</em>. For a specific flow, tstat calculates a number of statistics of all the packets transmitted over this flow, and then generate a log for such flow with multiple attributes (statistics). A log file is arranged as a simple table where each column is associated to specific information and each row reports the flow during a connection. The log information is a summary of the flow properties. For instance, in the TCP log we can find columns like the starting time of a TCP connection, its duration, the number of sent and received packets, the observed Round Trip Time.
![](tstat.png)

In this lab, since the focus is on the development of logistic regression from scratch, we only consider a portion of the dataset for simplicity. The data can be found in `log_tcp_part.csv`, in which there are multiple columns, the last one is the class label, indicating the flow is from either **google** or **youtube**, and the rest are features. Your job is a binary classification task to classify the domain of each flow (row) **from scratch**, including:
- Build a logistic regression model,
- Evaluate the performance.

1. Load the dataset.
2. Get the list of features (columns 1 to 10).
3. Add a new column and assign numerical class labels of -1 and 1 to google and youtube.
4. Answering the following questions:
    - How many features do we have?
    - How many samples do we have in total?
    - How many samples do we have for each class? Are they similar?

In [2]:
df_tcp = pd.read_csv('log_tcp_part.csv')
features = df_tcp.columns[:-1] # Remove class
df_tcp.replace({
    "class": {
        "google": -1,
        "youtube": 1,
    }
}, inplace=True)

df_tcp

/tmp/ipykernel_226018/230400442.py:3: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df_tcp.replace({


c_msgsize_count  c_pktsize6  c_msgsize4  s_msgsize4  s_pktsize2  \
0                    1           0           0           0        1418   
1                    1           0           0           0           0   
2                    1           0           0           0           0   
3                    1           0           0           0        1418   
4                    1           0           0           0        1418   
...                ...         ...         ...         ...         ...   
19995                4           0          37           0        1418   
19996                6          45          45          57        1418   
19997                4           0        1205           0         531   
19998                4           0         690           0         767   
19999                1           0           0           0           0   

       s_rtt_cnt  s_rtt_std  s_msgsize5  c_msgsize6    c_sit3  class  
0              0   0.000000           0           0     0.000     -1  
1              3   0.466732           0           0     0.000     -1  
2              3   0.413304           0           0     0.000     -1  
3              1   0.000000           0           0     0.000     -1  
4              0   0.000000           0           0     0.000     -1  
...          ...        ...         ...         ...       ...    ...  
19995          3  22.224528           0           0     3.334      1  
19996          2   0.000000          45          45     1.252      1  
19997          4  15.323660           0           0  4975.694      1  
19998          4  17.997651           0           0  1719.125      1  
19999          1   0.000000           0           0     0.000      1  

[20000 rows x 11 columns]

In [41]:
num_features = features.size
num_samples = len(df_tcp)
num_google = len(df_tcp.loc[df_tcp["class"] == -1])
num_youtube = len(df_tcp.loc[df_tcp["class"] == 1])

print(f"Number of features: {num_features}")
print(f"Number of samples: {num_samples}")
print(f"Number of samples of google: {num_google}")
print(f"Number of samples of youtube: {num_youtube}")

Number of features: 10
Number of samples: 20000
Number of samples of google: 10000
Number of samples of youtube: 10000


### 2. Implement your logistic regression learning algorithm
Here you will need to construct a class in which you need to define two functions besides the class initialization:
- `fit`. In this method you will perform ERM. Learn the parameters of the model (i.e., the hypothesis h) from training with gradient descent
- `predict`. In this method given one  sample x (or more) you will perform the inference $sign(h(x))$ to obtain class labels.

Hints:

- The linear function used in the logistic regression is the following: $h(x)=w^T x +b $, where b is a scalar bias.
- Logistic loss: $L((x,y),h)=\log(1+e^{-y h(x)})$
- ERM: $\min_{w,b} f(w,b)=\frac{1}{m}\sum_{i=1}^{m} \log(1+e^{-y^{(i)} h(x^{(i)})})$
- Gradient for weight: $\nabla_w f(w,b) = \frac{1}{m} \sum_i \frac{-y^{(i)}x^{(i)}}{(1+e^{y^{(i)}h(x^{(i)})})}$
- Gradient for bias: $\nabla_b f(w,b)= \frac{1}{m} \sum_i \frac{-y^{(i)}}{(1+e^{y^{(i)}h(x^{(i)})})}$
- Update the parameters: $w \leftarrow w - \alpha \nabla w$, $b \leftarrow b - \alpha  \nabla b$

Notice that the sigmoid function $f(z) = \frac{1}{1 + e^{-z}}$ appears multiple times. You can write also a method for the sigmoid function to help you in the computation. By considering f(z), the gradients rewrite as:

- Gradient for weight: $\nabla_w f(w,b) = \frac{1}{m} \sum_i ({f(h(x^{(i)})) - y^{(i)}})x^{(i)}$
- Gradient for bias: $\nabla_b f(w,b) = \frac{1}{m} \sum_i ({f(h(x^{(i)})) - y^{(i)}})$

In [176]:
def sigmoid(z):
    return 1/(1+np.exp(np.negative(z)))

class LogisticRegression:
    def __init__(self, learning_rate, num_iterations):
        self.learning_rate = learning_rate
        self.num_iterations = num_iterations


    def h(self, X):
        return np.dot(X, self.w) + self.b
    
    
    def gradient_step_w(self, m, X, y):
        h = self.h(X)
        f = sigmoid(h)
        s = np.dot(X.T, np.subtract(f, y))

        return s/m
    

    def gradient_step_b(self, m, X, y):
        h = self.h(X)
        f = sigmoid(h)
        s = np.subtract(f, y).sum()
        
        return s/m


    def fit(self, X, y):
        self.w = np.zeros((X.shape[1]))
        self.b = 0
        m = len(X)
        
        for i in range(self.num_iterations):
            w_step = self.gradient_step_w(m, X, y)
            b_step = self.gradient_step_b(m, X, y)

            self.w -= self.learning_rate*w_step
            self.b -= self.learning_rate*b_step

            y_predict = np.transpose(self.predict(X))==y
            correct_predictions = np.count_nonzero(y_predict == True)
            accuracy = correct_predictions/len(y)
            print(accuracy)
        

    def predict(self, X):
        if self.w is None or self.b is None:
            raise ValueError
        
        p = self.h(X)
        return np.sign(p)

### 3. Use the model
- Initialize your model with predefined learning rate of `0.1` and iterations of `100`.
- Fit your model with features and targets.
- Get the prediction with features.

In [177]:
from sklearn.model_selection import train_test_split

x_train, x_test, y_train, y_test = train_test_split(df_tcp.drop(columns=["class"], inplace=False), df_tcp["class"])

lr = LogisticRegression(0.1, 100)
lr.fit(x_train, y_train.values)

0.5768
0.5845333333333333
0.5632
0.6148
0.5904666666666667
0.617
0.5955333333333334
0.5915333333333334
0.6082666666666666
0.5925333333333334
0.6115333333333334
0.5924666666666667
0.6012666666666666
0.5922666666666667
0.6109333333333333
0.5952
0.5922
0.5996666666666667
0.5904666666666667
0.6062
0.5915333333333334
0.5988
0.5916
0.5979333333333333
0.5917333333333333
0.5962
0.5933333333333334
0.5955333333333334
0.5945333333333334
0.5947333333333333
0.5946
0.5946666666666667
0.5947333333333333
0.5946666666666667
0.5946666666666667
0.5946666666666667
0.5946
0.5946
0.5946666666666667
0.5945333333333334
0.5946666666666667
0.5945333333333334
0.5944666666666667
0.5946
0.5945333333333334
0.5946
0.5946
0.5946666666666667
0.5946
0.5945333333333334
0.5946666666666667
0.5946
0.5946
0.5946
0.5946666666666667
0.5945333333333334
0.5946
0.5946666666666667
0.5945333333333334
0.5946666666666667
0.5946666666666667
0.5946
0.5947333333333333
0.5946666666666667
0.5947333333333333
0.5946
0.5947333333333333
0.59

/tmp/ipykernel_226018/1018497028.py:2: RuntimeWarning: overflow encountered in exp
  return 1/(1+np.exp(np.negative(z)))
/tmp/ipykernel_226018/1018497028.py:2: RuntimeWarning: overflow encountered in exp
  return 1/(1+np.exp(np.negative(z)))
/tmp/ipykernel_226018/1018497028.py:2: RuntimeWarning: overflow encountered in exp
  return 1/(1+np.exp(np.negative(z)))
/tmp/ipykernel_226018/1018497028.py:2: RuntimeWarning: overflow encountered in exp
  return 1/(1+np.exp(np.negative(z)))
/tmp/ipykernel_226018/1018497028.py:2: RuntimeWarning: overflow encountered in exp
  return 1/(1+np.exp(np.negative(z)))
/tmp/ipykernel_226018/1018497028.py:2: RuntimeWarning: overflow encountered in exp
  return 1/(1+np.exp(np.negative(z)))
/tmp/ipykernel_226018/1018497028.py:2: RuntimeWarning: overflow encountered in exp
  return 1/(1+np.exp(np.negative(z)))
/tmp/ipykernel_226018/1018497028.py:2: RuntimeWarning: overflow encountered in exp
  return 1/(1+np.exp(np.negative(z)))
/tmp/ipykernel_226018/1018497028

In [174]:
y_predict = np.transpose(lr.predict(x_test))==y_test.values
correct_predictions = np.count_nonzero(y_predict == True)
accuracy = correct_predictions/len(y_test)

accuracy

0.6056

In [175]:
y_predict = np.transpose(lr.predict(x_train))==y_train.values
correct_predictions = np.count_nonzero(y_predict == True)
accuracy = correct_predictions/len(y_train)

accuracy

0.5965333333333334

### 4. Model evaluation
With predicted class labels and ground truths, we now evaluate the model performance through confusion matrix and numerical metrics. Specifically, you need to derive the following:
- Confusion matrix - Note that, you should indicate the corresponding quantity of each element in the table. Here positive is class 1 and negative is class -1:
\begin{array}{|c|c|c|}
\hline
 & \textbf{Predicted Positive} & \textbf{Predicted Negative} \\
\hline
\textbf{Actual Positive} & \text{True Positive (TP)} & \text{False Negative (FN)} \\
\hline
\textbf{Actual Negative} & \text{False Positive (FP)} & \text{True Negative (TN)} \\
\hline
\end{array}
- Precision of each class and the average value:
$\frac{\text{True Positive (TP)}}{\text{True Positive (TP) + False Positive (FP)}}$
- Recall of each class and the average value:
$\frac{\text{True Positive (TP)}}{\text{True Positive (TP) + False Negative (FN)}}$
- F1-score of each class and the average value:
$F_1 = \frac{2 \times \text{Precision} \times \text{Recall}}{\text{Precision} + \text{Recall}}$
- Accuracy:
$\frac{\text{True Positive (TP) + True Negative (TN)}}{\text{True Positive (TP) + True Negative (TN) + False Positive (FP) + False Negative (FN)}}$
- Answering the following questions:
    - Do you have same performance between classes? If not, which one performs better?
    - Change the parameters of learning rate or number of iterations. Do you have same performance? Better or Worse? Why?

In [ ]:
# your answers here